# Transit Speed Visualization Concept #

In [1]:
import boto3
from boto3.dynamodb.conditions import Key, Attr
import branca.colormap as cm
import folium
import json
import numpy as np
import pandas as pd

import config as cfg

## Load Route Shapes, Assign Average Speeds, and Map Speeds to Colors ##

In [2]:
#Load the geojson file

#Query the dynamoDB for all speed data, in this case all speeds above 0
dynamodb = boto3.resource('dynamodb',
                          region_name=cfg.REGION,
                          aws_access_key_id=cfg.ACCESS_ID,
                          aws_secret_access_key=cfg.ACCESS_KEY
                          )
table = dynamodb.Table('KCM_Bus_Routes')
response = table.scan(
    FilterExpression=Attr('avg_speed').gt(0)
)

In [3]:
#Put the data in a dictionary to easily reference from when adding speeds to the geojson shapes
items = response['Items']
route_lookup = {}
for item in items:
    route_id = int(item['route_id'])
    route_lookup[route_id] = {'avg_speed_m_s': float(item['avg_speed']),
                              'local_express_code': str(item['local_express_code']),
                              'historic_speeds': item['historic_speeds']}

In [4]:
#Read in geojson route geoJson, add a new property for avg speed, keep track of min/max speeds
speeds = np.ones(0)
with open('kcm_routes.geojson', 'r') as f:
    kcm_routes = json.load(f)
for feature in kcm_routes['features']:
    route_id = feature['properties']['ROUTE_ID']
    if route_id in route_lookup.keys():
        feature['properties']['AVG_SPEED_M_S'] = route_lookup[route_id]['avg_speed_m_s']
        speeds = np.append(speeds, route_lookup[route_id]['avg_speed_m_s'])
    else:
        feature['properties']['AVG_SPEED_M_S'] = 0
with open('kcm_routes_modified.geojson', 'w+') as f:
    json.dump(kcm_routes, f, indent=2)

#Create the color mapping for speeds
linear = cm.LinearColormap(['red', 'green'], vmin=np.percentile(speeds, 1), vmax=np.percentile(speeds, 75))

## Plot Map of Average Route Speeds ##

In [9]:
#Read in route shapefile and give it the style function above
kcm_routes = folium.GeoJson('kcm_routes_modified.geojson',
                            style_function=lambda feature: {
                                'color': linear(feature['properties']['AVG_SPEED_M_S']),
                                'weight': 2}
                            )
#Read in the census data/shapefile and create a choropleth based on income
seattle_tracts_df = pd.read_csv('seattle_census_tracts_2010_data.csv')
seattle_tracts_df['GEO_ID'] = seattle_tracts_df['GEO_ID'].astype(str)
seattle_tracts_df['mean_income'] = pd.to_numeric(seattle_tracts_df['mean_income'], errors='coerce')
seattle_tracts_df = seattle_tracts_df.dropna()
seattle_tracts = folium.Choropleth(geo_data='seattle_census_tracts_2010.geojson',
                                  name='Socioeconomic Data',
                                  data=seattle_tracts_df,
                                  columns=['GEO_ID', 'mean_income'],
                                  key_on='feature.properties.GEOID10',
                                  fill_color='PuBu',
                                  fill_opacity=0.7,
                                  line_opacity=0.4,
                                  legend_name='mean income'
                                  )

In [10]:
#Draw map using the updated kcm_routes with avg speed data and choropleth from census data
m = folium.Map(location=[47.606209, -122.332069],
               zoom_start=11,
               prefer_canvas=True
              )
seattle_tracts.add_to(m)
kcm_routes.add_to(m)
linear.caption = 'Average Speed (m/s)'
linear.add_to(m)
folium.LayerControl().add_to(m)
m